# Doc2Vec model
> * Positive or Negative

In [1]:
import os
from glob import glob
import pandas as pd
import html
import itertools
import pickle
import re

from collections import namedtuple
from gensim.models import doc2vec
import multiprocessing
from konlpy.tag import Mecab
from konlpy.utils import pprint
import numpy as np
from ckonlpy.tag import Twitter as ctwitter
mecab = Mecab()
ct = ctwitter()

C:\Users\pc\Anaconda3\lib\site-packages\gensim\utils.py:860: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [2]:
from sklearn.linear_model import LogisticRegression
from gensim.models.doc2vec import TaggedDocument
from sklearn.model_selection import train_test_split

In [3]:
import multiprocessing
cores = multiprocessing.cpu_count()

In [4]:
from tqdm import tqdm
tqdm.pandas(desc="progress-bar")

In [5]:
TaggedDocument = namedtuple('TaggedDocument', 'words tags')

# Doc2Vec 생성

* vector size
 [ 1000, 2000 ]

In [7]:
rawdata = pd.read_csv('./data/sentiment_data/raw_data_for_sentiment.txt',header=None,encoding='utf-8')
print (rawdata.shape)

(491510, 2)


### tagging twitter

In [8]:
# twitter
def tokenize1(doc):
    return ['/'.join(t) for t in ct.pos(doc)]

In [14]:
raw_doc_ct = [(tokenize1(rawdata.loc[idx][0]), rawdata.loc[idx][1]) for idx in rawdata.index]
pickle.dump(raw_doc_ct, open('./data/pre_data/tagged_data/pre_data_by_ct_for_sentiment_analysis.pickled','wb'))

In [15]:
tagged_ct = [TaggedDocument(d, [c]) for d, c in raw_doc_ct]
pickle.dump(tagged_ct, open('./data/pre_data/tagged_data/pre_by_ct_data_tagged_run_docs.pickled','wb'))

In [16]:
del raw_doc_ct

#### model 만들기

In [ ]:
tagged_ct = pickle.load(open('./data/pre_data/tagged_data/pre_by_ct_data_tagged_run_docs.pickled','rb'))

In [17]:
train, test = train_test_split(tagged_ct, test_size=0.1, random_state=42)

pickle.dump(train, open('./data/pre_data/train_test_Data/pre_by_ct_train.pickled','wb'))
pickle.dump(test, open('./data/pre_data/train_test_Data/pre_by_ct_test.pickled','wb'))

In [ ]:
train = pickle.load(open('./data/pre_data/train_test_Data/pre_by_ct_train.pickled','rb'))
test = pickle.load(open('./data/pre_data/train_test_Data/pre_by_ct_test.pickled','rb'))

In [18]:
%%time
doc_vectorizer = doc2vec.Doc2Vec(size=500, workers=8,dbow_words=1, window=5, alpha=0.025, min_alpha=0.025, seed=1234)
doc_vectorizer.build_vocab(tqdm(train))
for epoch in tqdm(range(15)):
    doc_vectorizer.train(tqdm(train), total_examples=doc_vectorizer.corpus_count, epochs=doc_vectorizer.iter)
    doc_vectorizer.alpha -= 0.002  # decrease the learning rate
    doc_vectorizer.min_alpha = doc_vectorizer.alpha  # fix the learning rate, no decay
#To save
doc_vectorizer.save('./model/doc2vec_size500_epoch15_window5_dbow_words_by_ct.model')
pprint(doc_vectorizer.most_similar('문재인/Noun'))
pprint(doc_vectorizer.most_similar('노무현/Noun'))
pprint(doc_vectorizer.most_similar('박근혜/Noun'))




  0%|          | 0/442359 [00:00<?, ?it/s]


  0%|          | 103/442359 [00:00<08:01, 918.26it/s]


  0%|          | 308/442359 [00:00<06:22, 1156.15it/s]


  0%|          | 540/442359 [00:00<04:40, 1576.57it/s]


  0%|          | 1801/442359 [00:00<01:48, 4077.76it/s]


  1%|          | 2775/442359 [00:00<01:28, 4956.67it/s]


  1%|          | 3936/442359 [00:00<01:11, 6121.62it/s]


  1%|          | 4736/442359 [00:00<01:08, 6373.15it/s]


  1%|▏         | 5781/442359 [00:00<01:03, 6863.62it/s]


  2%|▏         | 6947/442359 [00:00<01:00, 7218.05it/s]


  2%|▏         | 7936/442359 [00:01<00:58, 7468.48it/s]


  2%|▏         | 8860/442359 [00:01<00:57, 7484.49it/s]


  2%|▏         | 9893/442359 [00:01<00:55, 7784.17it/s]


  2%|▏         | 10835/442359 [00:01<00:54, 7868.15it/s]


  3%|▎         | 12049/442359 [00:01<00:52, 8145.48it/s]


  3%|▎         | 13532/442359 [00:01<00:50, 8567.93it/s]


  3%|▎         | 14715/442359 [00:01<00:48, 8761.40it/s]


  4%|▎         | 15872/4

  2%|▏         | 9886/442359 [00:04<03:14, 2226.86it/s]



  2%|▏         | 10359/442359 [00:04<03:09, 2280.92it/s]



  2%|▏         | 10793/442359 [00:04<03:06, 2315.22it/s]



  3%|▎         | 11203/442359 [00:04<03:04, 2342.28it/s]



  3%|▎         | 11732/442359 [00:04<02:59, 2393.73it/s]



  3%|▎         | 12293/442359 [00:05<02:56, 2439.89it/s]



  3%|▎         | 12899/442359 [00:05<02:52, 2495.20it/s]



  3%|▎         | 13323/442359 [00:05<02:49, 2528.23it/s]



  3%|▎         | 13745/442359 [00:05<02:48, 2545.90it/s]



  3%|▎         | 14218/442359 [00:05<02:45, 2580.38it/s]



  3%|▎         | 14765/442359 [00:05<02:42, 2627.59it/s]



  3%|▎         | 15305/442359 [00:05<02:40, 2666.66it/s]



  4%|▎         | 15750/442359 [00:05<02:40, 2665.59it/s]



  4%|▎         | 16137/442359 [00:06<02:38, 2681.54it/s]



  4%|▍         | 16645/442359 [00:06<02:37, 2707.82it/s]



  4%|▍         | 17225/442359 [00:06<02:35, 2738.81it/s]



  4%|▍         | 17657/442359 [00:06<02:3

 31%|███       | 135700/442359 [00:36<01:22, 3696.63it/s]



 31%|███       | 136134/442359 [00:36<01:22, 3697.26it/s]



 31%|███       | 136556/442359 [00:36<01:22, 3695.66it/s]



 31%|███       | 136974/442359 [00:37<01:22, 3696.65it/s]



 31%|███       | 137406/442359 [00:37<01:22, 3696.82it/s]



 31%|███       | 137798/442359 [00:37<01:22, 3695.71it/s]



 31%|███       | 138171/442359 [00:37<01:22, 3693.42it/s]



 31%|███▏      | 138745/442359 [00:37<01:22, 3697.57it/s]



 31%|███▏      | 139152/442359 [00:37<01:21, 3697.76it/s]



 32%|███▏      | 139546/442359 [00:37<01:21, 3698.68it/s]



 32%|███▏      | 139940/442359 [00:37<01:21, 3699.01it/s]



 32%|███▏      | 140331/442359 [00:37<01:21, 3698.97it/s]



 32%|███▏      | 140856/442359 [00:38<01:21, 3702.64it/s]



 32%|███▏      | 141344/442359 [00:38<01:21, 3704.35it/s]



 32%|███▏      | 141767/442359 [00:38<01:21, 3704.74it/s]



 32%|███▏      | 142177/442359 [00:38<01:21, 3704.40it/s]



 32%|███▏      | 142614/

 60%|█████▉    | 263790/442359 [01:09<00:46, 3812.88it/s]



 60%|█████▉    | 264431/442359 [01:09<00:46, 3814.91it/s]



 60%|█████▉    | 265027/442359 [01:09<00:46, 3816.62it/s]



 60%|██████    | 265473/442359 [01:09<00:46, 3817.42it/s]



 60%|██████    | 265909/442359 [01:09<00:46, 3817.20it/s]



 60%|██████    | 266342/442359 [01:09<00:46, 3817.55it/s]



 60%|██████    | 266830/442359 [01:09<00:45, 3818.84it/s]



 60%|██████    | 267262/442359 [01:09<00:45, 3819.27it/s]



 61%|██████    | 267686/442359 [01:10<00:45, 3817.89it/s]



 61%|██████    | 268144/442359 [01:10<00:45, 3817.37it/s]



 61%|██████    | 268656/442359 [01:10<00:45, 3818.67it/s]



 61%|██████    | 269239/442359 [01:10<00:45, 3820.97it/s]



 61%|██████    | 269702/442359 [01:10<00:45, 3822.11it/s]



 61%|██████    | 270151/442359 [01:10<00:45, 3820.83it/s]



 61%|██████    | 270582/442359 [01:10<00:44, 3820.59it/s]



 61%|██████▏   | 271145/442359 [01:10<00:44, 3821.19it/s]



 61%|██████▏   | 271787/

 88%|████████▊ | 388103/442359 [01:41<00:14, 3826.85it/s]



 88%|████████▊ | 388571/442359 [01:41<00:14, 3826.59it/s]



 88%|████████▊ | 388934/442359 [01:41<00:13, 3826.35it/s]



 88%|████████▊ | 389390/442359 [01:41<00:13, 3824.54it/s]



 88%|████████▊ | 389933/442359 [01:41<00:13, 3825.74it/s]



 88%|████████▊ | 390309/442359 [01:42<00:13, 3825.03it/s]



 88%|████████▊ | 390668/442359 [01:42<00:13, 3824.00it/s]



 88%|████████▊ | 391158/442359 [01:42<00:13, 3824.79it/s]



 89%|████████▊ | 391549/442359 [01:42<00:13, 3824.38it/s]



 89%|████████▊ | 392001/442359 [01:42<00:13, 3824.83it/s]



 89%|████████▊ | 392476/442359 [01:42<00:13, 3825.28it/s]



 89%|████████▉ | 392872/442359 [01:42<00:12, 3824.58it/s]



 89%|████████▉ | 393364/442359 [01:42<00:12, 3824.34it/s]



 89%|████████▉ | 393935/442359 [01:42<00:12, 3825.23it/s]



 89%|████████▉ | 394373/442359 [01:43<00:12, 3825.13it/s]



 89%|████████▉ | 394763/442359 [01:43<00:12, 3824.53it/s]



 89%|████████▉ | 395137/

...

[('손학규/Noun', 0.5002566576004028),
 ('안철수/Noun', 0.49057313799858093),
 ('문/Noun', 0.490328311920166),
 ('정세균/Noun', 0.4482108950614929),
 ('김종인/Noun', 0.4111119508743286),
 ('김무성/Noun', 0.3970564007759094),
 ('추미애/Noun', 0.38549983501434326),
 ('박근혜/Noun', 0.3850722908973694),
 ('김한길/Noun', 0.3749983012676239),
 ('이태근/Noun', 0.37190571427345276)]


C:\Users\pc\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  # Remove the CWD from sys.path while we load stuff.


[('이명박/Noun', 0.6669771671295166),
 ('노/Noun', 0.6334550380706787),
 ('박근혜/Noun', 0.6322810649871826),
 ('김영삼/Noun', 0.5668947100639343),
 ('노태우/Noun', 0.5082482099533081),
 ('박정희/Noun', 0.4958740174770355),
 ('김대중/Noun', 0.4927920699119568),
 ('박/Noun', 0.4717112183570862),
 ('金大中/Foreign', 0.4337949752807617),
 ('盧/Foreign', 0.4288804531097412)]


C:\Users\pc\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  # This is added back by InteractiveShellApp.init_path()


[('이명박/Noun', 0.7279862761497498),
 ('박/Noun', 0.6989729404449463),
 ('노무현/Noun', 0.6322810649871826),
 ('김영삼/Noun', 0.5701685547828674),
 ('노/Noun', 0.5502873659133911),
 ('김대중/Noun', 0.5330442190170288),
 ('김/Noun', 0.49240848422050476),
 ('노태우/Noun', 0.48640215396881104),
 ('朴/Foreign', 0.4846562147140503),
 ('박정희/Noun', 0.45552802085876465)]
Wall time: 2h 44min 20s


In [19]:
%%time
doc_vectorizer = doc2vec.Doc2Vec(size=1000, workers=8,dbow_words=1, window=5, alpha=0.025, min_alpha=0.025, seed=1234)
doc_vectorizer.build_vocab(tqdm(train))
for epoch in tqdm(range(15)):
    doc_vectorizer.train(tqdm(train), total_examples=doc_vectorizer.corpus_count, epochs=doc_vectorizer.iter)
    doc_vectorizer.alpha -= 0.002  # decrease the learning rate
    doc_vectorizer.min_alpha = doc_vectorizer.alpha  # fix the learning rate, no decay
#To save
doc_vectorizer.save('./model/doc2vec_size1000_epoch15_window5_dbow_words_by_ct.model')
pprint(doc_vectorizer.most_similar('문재인/Noun'))
pprint(doc_vectorizer.most_similar('노무현/Noun'))
pprint(doc_vectorizer.most_similar('박근혜/Noun'))




  0%|          | 0/442359 [00:00<?, ?it/s]


  0%|          | 722/442359 [00:00<01:03, 6931.91it/s]


  0%|          | 1196/442359 [00:00<01:15, 5853.95it/s]


  0%|          | 1633/442359 [00:00<01:22, 5311.19it/s]


  0%|          | 2144/442359 [00:00<01:23, 5272.86it/s]


  1%|          | 2610/442359 [00:00<01:25, 5130.05it/s]


  1%|          | 3090/442359 [00:00<01:26, 5074.60it/s]


  1%|          | 3859/442359 [00:00<01:20, 5442.35it/s]


  1%|          | 4578/442359 [00:00<01:17, 5664.33it/s]


  1%|          | 5432/442359 [00:00<01:13, 5973.39it/s]


  1%|▏         | 6279/442359 [00:01<01:10, 6219.79it/s]


  2%|▏         | 7150/442359 [00:01<01:07, 6443.37it/s]


  2%|▏         | 8054/442359 [00:01<01:05, 6657.19it/s]


  2%|▏         | 8901/442359 [00:01<01:03, 6794.81it/s]


  2%|▏         | 9820/442359 [00:01<01:02, 6963.94it/s]


  2%|▏         | 10669/442359 [00:01<01:01, 7050.27it/s]


  3%|▎         | 11510/442359 [00:01<01:00, 7098.64it/s]


  3%|▎         | 12332/

 26%|██▋       | 116781/442359 [00:14<00:39, 8191.45it/s]


 27%|██▋       | 117682/442359 [00:14<00:39, 8193.64it/s]


 27%|██▋       | 118567/442359 [00:14<00:39, 8194.68it/s]


 27%|██▋       | 119444/442359 [00:14<00:39, 8198.55it/s]


 27%|██▋       | 120451/442359 [00:14<00:39, 8211.78it/s]


 27%|██▋       | 121385/442359 [00:14<00:39, 8219.34it/s]


 28%|██▊       | 122303/442359 [00:14<00:38, 8223.50it/s]


 28%|██▊       | 123218/442359 [00:14<00:38, 8230.16it/s]


 28%|██▊       | 124258/442359 [00:15<00:38, 8244.47it/s]


 28%|██▊       | 125208/442359 [00:15<00:38, 8252.12it/s]


 29%|██▊       | 126273/442359 [00:15<00:38, 8267.74it/s]


 29%|██▉       | 127257/442359 [00:15<00:38, 8273.57it/s]


 29%|██▉       | 128221/442359 [00:15<00:37, 8281.25it/s]


 29%|██▉       | 129218/442359 [00:15<00:37, 8292.54it/s]


 29%|██▉       | 130203/442359 [00:15<00:37, 8302.39it/s]


 30%|██▉       | 131176/442359 [00:15<00:37, 8303.98it/s]


 30%|██▉       | 132113/442359 [00:15<00

 87%|████████▋ | 383864/442359 [00:42<00:06, 9071.44it/s]


 87%|████████▋ | 384775/442359 [00:42<00:06, 9071.28it/s]


 87%|████████▋ | 385683/442359 [00:42<00:06, 9068.92it/s]


 87%|████████▋ | 386566/442359 [00:42<00:06, 9067.48it/s]


 88%|████████▊ | 387439/442359 [00:42<00:06, 9065.59it/s]


 88%|████████▊ | 388429/442359 [00:42<00:05, 9067.51it/s]


 88%|████████▊ | 389427/442359 [00:42<00:05, 9069.81it/s]


 88%|████████▊ | 390448/442359 [00:43<00:05, 9072.43it/s]


 88%|████████▊ | 391404/442359 [00:43<00:05, 9072.69it/s]


 89%|████████▊ | 392354/442359 [00:43<00:05, 9072.80it/s]


 89%|████████▉ | 393351/442359 [00:43<00:05, 9074.84it/s]


 89%|████████▉ | 394305/442359 [00:43<00:05, 9075.67it/s]


 89%|████████▉ | 395256/442359 [00:43<00:05, 9076.01it/s]


 90%|████████▉ | 396198/442359 [00:43<00:05, 9074.89it/s]


 90%|████████▉ | 397117/442359 [00:43<00:04, 9074.29it/s]


 90%|████████▉ | 398057/442359 [00:43<00:04, 9075.01it/s]


 90%|█████████ | 398980/442359 [00:43<00

 11%|█         | 49738/442359 [00:32<04:13, 1549.70it/s]



 11%|█▏        | 50034/442359 [00:32<04:12, 1552.38it/s]



 11%|█▏        | 50217/442359 [00:32<04:12, 1552.65it/s]



 11%|█▏        | 50484/442359 [00:32<04:11, 1555.90it/s]



 11%|█▏        | 50687/442359 [00:32<04:12, 1551.76it/s]



 12%|█▏        | 51031/442359 [00:32<04:11, 1556.71it/s]



 12%|█▏        | 51239/442359 [00:32<04:11, 1557.44it/s]



 12%|█▏        | 51438/442359 [00:33<04:11, 1557.09it/s]



 12%|█▏        | 51700/442359 [00:33<04:10, 1558.36it/s]



 12%|█▏        | 51889/442359 [00:33<04:10, 1557.10it/s]



 12%|█▏        | 52119/442359 [00:33<04:10, 1558.33it/s]



 12%|█▏        | 52373/442359 [00:33<04:09, 1560.04it/s]



 12%|█▏        | 52654/442359 [00:33<04:09, 1560.82it/s]



 12%|█▏        | 52846/442359 [00:33<04:09, 1560.82it/s]



 12%|█▏        | 53067/442359 [00:33<04:09, 1561.61it/s]



 12%|█▏        | 53254/442359 [00:34<04:09, 1561.87it/s]



 12%|█▏        | 53426/442359 [00:34<04:

 27%|██▋       | 119113/442359 [01:09<03:09, 1709.33it/s]



 27%|██▋       | 119528/442359 [01:09<03:08, 1712.90it/s]



 27%|██▋       | 119784/442359 [01:10<03:08, 1710.58it/s]



 27%|██▋       | 120113/442359 [01:10<03:08, 1710.48it/s]



 27%|██▋       | 120365/442359 [01:10<03:08, 1710.75it/s]



 27%|██▋       | 120713/442359 [01:10<03:07, 1711.66it/s]



 27%|██▋       | 120940/442359 [01:10<03:07, 1711.59it/s]



 27%|██▋       | 121273/442359 [01:10<03:07, 1711.36it/s]



 27%|██▋       | 121473/442359 [01:10<03:07, 1711.66it/s]



 28%|██▊       | 121776/442359 [01:11<03:07, 1710.48it/s]



 28%|██▊       | 122083/442359 [01:11<03:07, 1712.14it/s]



 28%|██▊       | 122350/442359 [01:11<03:06, 1711.39it/s]



 28%|██▊       | 122580/442359 [01:11<03:06, 1711.92it/s]



 28%|██▊       | 122918/442359 [01:11<03:06, 1712.26it/s]



 28%|██▊       | 123200/442359 [01:11<03:06, 1712.63it/s]



 28%|██▊       | 123508/442359 [01:12<03:06, 1713.19it/s]



 28%|██▊       | 123701/

...

[('문/Noun', 0.4086710214614868),
 ('안철수/Noun', 0.37273794412612915),
 ('손학규/Noun', 0.3658345341682434),
 ('박근혜/Noun', 0.3282366991043091),
 ('추미애/Noun', 0.31241434812545776),
 ('박/Noun', 0.3008478879928589),
 ('정세균/Noun', 0.29837095737457275),
 ('김/Noun', 0.27643370628356934),
 ('이태근/Noun', 0.2725076675415039),
 ('김종인/Noun', 0.270829439163208)]


C:\Users\pc\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  # Remove the CWD from sys.path while we load stuff.


[('노/Noun', 0.5595223903656006),
 ('이명박/Noun', 0.5381197333335876),
 ('박근혜/Noun', 0.5285188555717468),
 ('김영삼/Noun', 0.44420289993286133),
 ('박/Noun', 0.40671515464782715),
 ('김대중/Noun', 0.37657052278518677),
 ('노태우/Noun', 0.371031790971756),
 ('박정희/Noun', 0.369931161403656),
 ('“金大中/Foreign', 0.3269265294075012),
 ('盧/Foreign', 0.32516300678253174)]


C:\Users\pc\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  # This is added back by InteractiveShellApp.init_path()


[('박/Noun', 0.6239805221557617),
 ('이명박/Noun', 0.5807033181190491),
 ('노무현/Noun', 0.5285188555717468),
 ('김영삼/Noun', 0.45922160148620605),
 ('노/Noun', 0.4499456584453583),
 ('김대중/Noun', 0.43308547139167786),
 ('김/Noun', 0.4209788143634796),
 ('金泳三/Foreign', 0.38907185196876526),
 ('朴/Foreign', 0.38408413529396057),
 ('노태우/Noun', 0.3768036961555481)]
Wall time: 4h 54min 35s


* size 1000, epoch 20 으로 모델 생성
* size 2000, epoch 2
0 으로 모델 생성

In [ ]:
%%time
doc_vectorizer = doc2vec.Doc2Vec(size=1500, workers=8,dbow_words=1, window=5, alpha=0.025, min_alpha=0.025, seed=1234)
doc_vectorizer.build_vocab(tqdm(train))
for epoch in tqdm(range(15)):
    doc_vectorizer.train(tqdm(train), total_examples=doc_vectorizer.corpus_count, epochs=doc_vectorizer.iter)
    doc_vectorizer.alpha -= 0.002  # decrease the learning rate
    doc_vectorizer.min_alpha = doc_vectorizer.alpha  # fix the learning rate, no decay
#To save
doc_vectorizer.save('./model/doc2vec_size1500_epoch15_window5_dbow_words_by_ct.model')
pprint(doc_vectorizer.most_similar('문재인/Noun'))
pprint(doc_vectorizer.most_similar('노무현/Noun'))
pprint(doc_vectorizer.most_similar('박근혜/Noun'))




  0%|          | 0/442359 [00:00<?, ?it/s]


  0%|          | 26/442359 [00:00<32:29, 226.91it/s]


  0%|          | 95/442359 [00:00<18:43, 393.54it/s]


  0%|          | 142/442359 [00:00<17:50, 413.05it/s]


  0%|          | 272/442359 [00:00<12:00, 613.76it/s]


  0%|          | 331/442359 [00:00<14:13, 517.63it/s]


  0%|          | 386/442359 [00:00<14:07, 521.35it/s]


  0%|          | 503/442359 [00:00<12:21, 595.97it/s]


  0%|          | 573/442359 [00:00<12:21, 595.80it/s]


  0%|          | 640/442359 [00:01<12:20, 596.89it/s]


  0%|          | 705/442359 [00:01<12:20, 596.44it/s]


  0%|          | 853/442359 [00:01<11:10, 658.51it/s]


  0%|          | 937/442359 [00:01<11:48, 623.40it/s]


  0%|          | 1028/442359 [00:01<11:32, 636.93it/s]


  0%|          | 1120/442359 [00:01<11:30, 638.74it/s]


  0%|          | 1279/442359 [00:01<10:43, 685.14it/s]


  0%|          | 1372/442359 [00:02<10:51, 676.94it/s]


  0%|          | 1467/442359 [00:02<10:53, 674.48it/s]

 11%|█         | 48277/442359 [00:36<05:01, 1308.98it/s]


 11%|█         | 48671/442359 [00:36<04:59, 1315.53it/s]


 11%|█         | 48920/442359 [00:37<04:58, 1318.68it/s]


 11%|█         | 49256/442359 [00:37<04:56, 1324.15it/s]


 11%|█         | 49631/442359 [00:37<04:55, 1330.43it/s]


 11%|█▏        | 49921/442359 [00:37<04:54, 1334.16it/s]


 11%|█▏        | 50470/442359 [00:37<04:51, 1345.26it/s]


 11%|█▏        | 50830/442359 [00:37<04:50, 1349.68it/s]


 12%|█▏        | 51158/442359 [00:37<04:49, 1350.77it/s]


 12%|█▏        | 51484/442359 [00:37<04:48, 1355.66it/s]


 12%|█▏        | 51771/442359 [00:38<04:47, 1356.75it/s]


 12%|█▏        | 52114/442359 [00:38<04:46, 1361.62it/s]


 12%|█▏        | 52377/442359 [00:38<04:46, 1362.92it/s]


 12%|█▏        | 52612/442359 [00:38<04:45, 1364.18it/s]


 12%|█▏        | 53006/442359 [00:38<04:44, 1370.55it/s]


 12%|█▏        | 53267/442359 [00:38<04:43, 1372.70it/s]


 12%|█▏        | 53632/442359 [00:38<04:42, 1378.29it/s]

 50%|████▉     | 221117/442359 [01:09<01:09, 3182.33it/s]


 50%|█████     | 221908/442359 [01:09<01:09, 3189.16it/s]


 50%|█████     | 222713/442359 [01:09<01:08, 3196.12it/s]


 51%|█████     | 223587/442359 [01:09<01:08, 3204.05it/s]


 51%|█████     | 224422/442359 [01:09<01:07, 3211.00it/s]


 51%|█████     | 225389/442359 [01:09<01:07, 3220.27it/s]


 51%|█████     | 226221/442359 [01:10<01:06, 3225.96it/s]


 51%|█████▏    | 227305/442359 [01:10<01:06, 3236.79it/s]


 52%|█████▏    | 228531/442359 [01:10<01:05, 3249.62it/s]


 52%|█████▏    | 229551/442359 [01:10<01:05, 3259.11it/s]


 52%|█████▏    | 230514/442359 [01:10<01:04, 3265.81it/s]


 52%|█████▏    | 231382/442359 [01:10<01:04, 3272.39it/s]


 52%|█████▏    | 232201/442359 [01:10<01:04, 3279.04it/s]


 53%|█████▎    | 233005/442359 [01:10<01:03, 3282.69it/s]


 53%|█████▎    | 233713/442359 [01:11<01:03, 3286.17it/s]


 53%|█████▎    | 234778/442359 [01:11<01:02, 3296.55it/s]


 53%|█████▎    | 235962/442359 [01:11<01

  8%|▊         | 34058/442359 [00:14<02:49, 2405.61it/s]



  8%|▊         | 34454/442359 [00:14<02:49, 2409.21it/s]



  8%|▊         | 34757/442359 [00:14<02:49, 2410.98it/s]



  8%|▊         | 35041/442359 [00:14<02:49, 2407.10it/s]



  8%|▊         | 35499/442359 [00:14<02:48, 2413.49it/s]



  8%|▊         | 35759/442359 [00:14<02:48, 2410.65it/s]



  8%|▊         | 36079/442359 [00:14<02:48, 2413.80it/s]



  8%|▊         | 36334/442359 [00:15<02:48, 2411.95it/s]



  8%|▊         | 36674/442359 [00:15<02:47, 2415.42it/s]



  8%|▊         | 36931/442359 [00:15<02:48, 2410.09it/s]



  8%|▊         | 37312/442359 [00:15<02:47, 2417.10it/s]



  8%|▊         | 37578/442359 [00:15<02:47, 2413.66it/s]



  9%|▊         | 37866/442359 [00:15<02:47, 2414.30it/s]



  9%|▊         | 38114/442359 [00:15<02:47, 2411.63it/s]



  9%|▊         | 38461/442359 [00:15<02:47, 2405.39it/s]



  9%|▉         | 38891/442359 [00:16<02:47, 2415.64it/s]



  9%|▉         | 39161/442359 [00:16<02:

 27%|██▋       | 121144/442359 [00:48<02:08, 2497.18it/s]



 27%|██▋       | 121388/442359 [00:48<02:08, 2496.85it/s]



 27%|██▋       | 121628/442359 [00:48<02:08, 2494.98it/s]



 28%|██▊       | 121866/442359 [00:48<02:08, 2494.24it/s]



 28%|██▊       | 122239/442359 [00:48<02:08, 2495.92it/s]



 28%|██▊       | 122487/442359 [00:49<02:08, 2495.49it/s]



 28%|██▊       | 122733/442359 [00:49<02:08, 2494.96it/s]



 28%|██▊       | 122994/442359 [00:49<02:08, 2494.78it/s]



 28%|██▊       | 123325/442359 [00:49<02:07, 2495.26it/s]



 28%|██▊       | 123576/442359 [00:49<02:07, 2494.03it/s]



 28%|██▊       | 124020/442359 [00:49<02:07, 2497.65it/s]



 28%|██▊       | 124313/442359 [00:49<02:07, 2495.30it/s]



 28%|██▊       | 124710/442359 [00:50<02:07, 2492.89it/s]



 28%|██▊       | 125267/442359 [00:50<02:06, 2497.63it/s]



 28%|██▊       | 125564/442359 [00:50<02:06, 2497.61it/s]



 28%|██▊       | 126013/442359 [00:50<02:06, 2496.65it/s]



 29%|██▊       | 126429/

...

[('문/Noun', 0.32342103123664856),
 ('안철수/Noun', 0.32046014070510864),
 ('박근혜/Noun', 0.2733606994152069),
 ('손학규/Noun', 0.26953262090682983),
 ('정세균/Noun', 0.26404130458831787),
 ('박/Noun', 0.25684207677841187),
 ('이태근/Noun', 0.25487202405929565),
 ('추미애/Noun', 0.2480897754430771),
 ('김/Noun', 0.24424037337303162),
 ('김종인/Noun', 0.24064478278160095)]


C:\Users\pc\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  # Remove the CWD from sys.path while we load stuff.


[('노/Noun', 0.4966657757759094),
 ('이명박/Noun', 0.4637715816497803),
 ('박근혜/Noun', 0.45839664340019226),
 ('김영삼/Noun', 0.35739022493362427),
 ('박/Noun', 0.3532511591911316),
 ('노태우/Noun', 0.32571685314178467),
 ('김대중/Noun', 0.3096764087677002),
 ('박정희/Noun', 0.3063104748725891),
 ('盧/Foreign', 0.2853247821331024),
 ('면노/Noun', 0.27595627307891846)]


C:\Users\pc\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  # This is added back by InteractiveShellApp.init_path()


[('박/Noun', 0.5678164958953857),
 ('이명박/Noun', 0.5159057974815369),
 ('노무현/Noun', 0.45839664340019226),
 ('노/Noun', 0.41735178232192993),
 ('김대중/Noun', 0.40184885263442993),
 ('김영삼/Noun', 0.39182573556900024),
 ('김/Noun', 0.38699352741241455),
 ('朴/Foreign', 0.3480609655380249),
 ('“朴/Foreign', 0.34784138202667236),
 ('노태우/Noun', 0.33617207407951355)]
Wall time: 3h 9min 46s


In [ ]:
%%time
doc_vectorizer = doc2vec.Doc2Vec(size=2000, workers=8,dbow_words=1, window=5, alpha=0.025, min_alpha=0.025, seed=1234)
doc_vectorizer.build_vocab(tqdm(train))
for epoch in tqdm(range(15)):
    doc_vectorizer.train(tqdm(train), total_examples=doc_vectorizer.corpus_count, epochs=doc_vectorizer.iter)
    doc_vectorizer.alpha -= 0.002  # decrease the learning rate
    doc_vectorizer.min_alpha = doc_vectorizer.alpha  # fix the learning rate, no decay
#To save
doc_vectorizer.save('./model/doc2vec_size2000_epoch15_window5_dbow_words_by_ct.model')
pprint(doc_vectorizer.most_similar('문재인/Noun'))
pprint(doc_vectorizer.most_similar('노무현/Noun'))
pprint(doc_vectorizer.most_similar('박근혜/Noun'))

  6%|▌         | 26587/442359 [00:24<06:20, 1091.61it/s]


 12%|█▏        | 51461/442359 [00:48<06:07, 1063.56it/s]


 17%|█▋        | 76618/442359 [01:12<05:45, 1057.14it/s]


 23%|██▎       | 103630/442359 [01:36<05:14, 1076.10it/s]


 29%|██▉       | 127542/442359 [01:58<04:51, 1079.31it/s]


...

 75%|███████▌  | 333301/442359 [03:00<00:58, 1849.38it/s]


 83%|████████▎ | 368900/442359 [03:19<00:39, 1845.76it/s]


 91%|█████████▏| 404227/442359 [03:39<00:20, 1842.20it/s]


 99%|█████████▉| 437098/442359 [03:59<00:02, 1824.10it/s]


100%|██████████| 442359/442359 [04:03<00:00, 1820.09it/s]

In [ ]:
del tagged_ct
del train
del test
del doc_vectorizer

### tagging mecab

In [ ]:
# mecab
def tokenize2(doc):
    return ['/'.join(t) for t in mecab.pos(doc)]

In [ ]:
raw_doc_mecab = [(tokenize2(rawdata.loc[idx][0]), rawdata.loc[idx][1]) for idx in rawdata.index]
pickle.dump(raw_doc_mecab, open('./data/pre_data/tagged_data/pre_data_by_mecab_for_sentiment_analysis.pickled','wb'))

In [ ]:
tagged_mecab = [TaggedDocument(d, [c]) for d, c in raw_doc_mecab]
pickle.dump(tagged_mecab, open('./data/pre_data/tagged_data/pre_by_mecab_data_tagged_run_docs.pickled','wb'))

In [ ]:
del raw_doc_mecab

#### model 만들기

In [ ]:
tagged_mecab = pickle.load(open('./data/pre_data/tagged_data/pre_by_mecab_data_tagged_run_docs.pickled','rb'))

In [ ]:
train2, test2 = train_test_split(tagged_mecab, test_size=0.1, random_state=42)

pickle.dump(train2, open('./data/pre_data/train_test_Data/pre_by_mecab_train.pickled','wb'))
pickle.dump(test2, open('./data/pre_data/train_test_Data/pre_by_mecab_test.pickled','wb'))

In [ ]:
train2 = pickle.load(open('./data/pre_data/train_test_Data/pre_by_mecab_train.pickled','rb'))
test2 = pickle.load(open('./data/pre_data/train_test_Data/pre_by_mecab_test.pickled','rb'))

In [ ]:
%%time
doc_vectorizer = doc2vec.Doc2Vec(size=500, workers=8,dbow_words=1, window=5, alpha=0.025, min_alpha=0.025, seed=1234)
doc_vectorizer.build_vocab(tqdm(train2))
for epoch in tqdm(range(15)):
    doc_vectorizer.train(tqdm(train), total_examples=doc_vectorizer.corpus_count, epochs=doc_vectorizer.iter)
    doc_vectorizer.alpha -= 0.002  # decrease the learning rate
    doc_vectorizer.min_alpha = doc_vectorizer.alpha  # fix the learning rate, no decay
#To save
doc_vectorizer.save('./model/doc2vec_size500_epoch15_window5_dbow_words_by_mecab.model')
pprint(doc_vectorizer.most_similar('문재인/Noun'))
pprint(doc_vectorizer.most_similar('노무현/Noun'))
pprint(doc_vectorizer.most_similar('박근혜/Noun'))

In [ ]:
%%time
doc_vectorizer = doc2vec.Doc2Vec(size=1000, workers=8,dbow_words=1, window=5, alpha=0.025, min_alpha=0.025, seed=1234)
doc_vectorizer.build_vocab(tqdm(train2))
for epoch in tqdm(range(15)):
    doc_vectorizer.train(tqdm(train), total_examples=doc_vectorizer.corpus_count, epochs=doc_vectorizer.iter)
    doc_vectorizer.alpha -= 0.002  # decrease the learning rate
    doc_vectorizer.min_alpha = doc_vectorizer.alpha  # fix the learning rate, no decay
#To save
doc_vectorizer.save('./model/doc2vec_size1000_epoch15_window5_dbow_words_by_mecab.model')
pprint(doc_vectorizer.most_similar('문재인/Noun'))
pprint(doc_vectorizer.most_similar('노무현/Noun'))
pprint(doc_vectorizer.most_similar('박근혜/Noun'))

* size 1000, epoch 20 으로 모델 생성
* size 2000, epoch 20 으로 모델 생성

In [ ]:
%%time
doc_vectorizer = doc2vec.Doc2Vec(size=1500, workers=8,dbow_words=1, window=5, alpha=0.025, min_alpha=0.025, seed=1234)
doc_vectorizer.build_vocab(tqdm(train2))
for epoch in tqdm(range(15)):
    doc_vectorizer.train(tqdm(train), total_examples=doc_vectorizer.corpus_count, epochs=doc_vectorizer.iter)
    doc_vectorizer.alpha -= 0.002  # decrease the learning rate
    doc_vectorizer.min_alpha = doc_vectorizer.alpha  # fix the learning rate, no decay
#To save
doc_vectorizer.save('./model/doc2vec_size1500_epoch15_window5_dbow_words_by_mecab.model')
pprint(doc_vectorizer.most_similar('문재인/Noun'))
pprint(doc_vectorizer.most_similar('노무현/Noun'))
pprint(doc_vectorizer.most_similar('박근혜/Noun'))

In [ ]:
%%time
doc_vectorizer = doc2vec.Doc2Vec(size=2000, workers=8,dbow_words=1, window=5, alpha=0.025, min_alpha=0.025, seed=1234)
doc_vectorizer.build_vocab(tqdm(train2))
for epoch in tqdm(range(15)):
    doc_vectorizer.train(tqdm(train), total_examples=doc_vectorizer.corpus_count, epochs=doc_vectorizer.iter)
    doc_vectorizer.alpha -= 0.002  # decrease the learning rate
    doc_vectorizer.min_alpha = doc_vectorizer.alpha  # fix the learning rate, no decay
#To save
doc_vectorizer.save('./model/doc2vec_size2000_epoch15_window5_dbow_words_by_mecab.model')
pprint(doc_vectorizer.most_similar('문재인/Noun'))
pprint(doc_vectorizer.most_similar('노무현/Noun'))
pprint(doc_vectorizer.most_similar('박근혜/Noun'))

In [ ]:
del tagged_mecab
del train2
del test2
del doc_vectorizer2